In [1]:
import os
import glob

import numpy as np
import pandas as pd
import pyarrow.parquet as pq

from plotly import express as px
import plotly.graph_objs as go

In [21]:
RESULT_DIR_TEMPLATE = 'results/result_*'

expms = {}

for record_dir in glob.glob(RESULT_DIR_TEMPLATE):
  org_loc = pq.read_table(os.path.join(record_dir,
                                       'organisms_locations')).to_pandas()
  # org_stat = pq.read_table(os.path.join(run1_results_dir,
  #                                       'organisms_stats')).to_pandas()
  # food_loc = pq.read_table(os.path.join(run1_results_dir,
  #                                       'food_locations')).to_pandas()
  food_stat = pq.read_table(os.path.join(record_dir,
                                        'eaten_food')).to_pandas()

  org_loc.reset_index(drop=True, inplace=True)
  # org_stat.reset_index(drop=True, inplace=True)
  # food_loc.reset_index(drop=True, inplace=True)
  food_stat.reset_index(drop=True, inplace=True)
  
  expms[record_dir] = {
    'org_loc': org_loc,
    'eaten_stat': food_stat,
  }
  
expms

{'results/result_iterations_5001_generation_time_4_elitism_20_genome_size_16-6-2_remove_dead_organisms_True653': {'org_loc':         index          x          y     theta  name  iteration  generation   
  0        3930  12.187379  13.080963  1.546092    Da       1001         250  \
  1        3984   7.015539   2.657761  2.600000     D       1001         250   
  2        3993   0.872536   1.668031  1.800000   Cap       1001         250   
  3        3996   8.268565   6.517998  1.400000    Ca       1001         250   
  4        4009  14.718921   6.889782  0.200000  Lisa       1001         250   
  ...       ...        ...        ...       ...   ...        ...         ...   
  155062   9635   7.710037   1.583033  0.000000  Lavi       2400         600   
  155063   9636   4.433823  12.755020  0.000000     K       2400         600   
  155064   9637   7.935933  17.499128  0.000000  Zose       2400         600   
  155065   9638   6.242968   7.256397  0.000000   Lic       2400         600 

In [3]:
def get_energy_traces_over_time(org_loc, window=80, legendgroup=''):
  moving_age_mean = org_loc[[
      'iteration', 'age'
  ]].groupby('iteration').mean().rolling(window).mean()

  moving_age_max = org_loc[['iteration', 'age'
                            ]].groupby('iteration').max().rolling(window).mean()

  moving_energy_mean = org_loc[[
      'iteration', 'energy'
  ]].groupby('iteration').mean().rolling(window).mean()

  moving_energy_max = org_loc[[
      'iteration', 'energy'
  ]].groupby('iteration').max().rolling(window).mean()

  x = np.arange(len(moving_age_max))

  ma_age = go.Scatter(
      x=x,
      y=moving_age_mean['age'],
      name=f'Moving Age Average {window=}',
      mode='lines',
      legendgroup=legendgroup,
  )
  mm_age = go.Scatter(x=x,
                      y=moving_age_max['age'],
                      name=f'Moving Age Max {window=}',
                      mode='lines',
                      legendgroup=legendgroup)
  ma_energy = go.Scatter(x=x,
                        y=moving_energy_mean['energy'],
                        name=f'Moving Energy Average {window=}',
                        mode='lines',
                        legendgroup=legendgroup)
  mm_energy = go.Scatter(x=x,
                        y=moving_energy_max['energy'],
                        name=f'Moving Energy Max {window=}',
                        mode='lines',
                        legendgroup=legendgroup)
  
  return mm_energy, ma_energy


In [4]:
layout = go.Layout(title='Evolution Statistics', xaxis=dict(title='Time'))

data = [
    trace
    for exp in expms for trace in get_energy_traces_over_time(expms[exp]['org_loc'], window=80, legendgroup=exp)
]

fig = go.Figure(data=data, layout=layout)
# # fig = go.Figure(data=[ma_age, mm_age, mm_energy, ma_energy], layout=layout)
fig.show()

# Food-to_Movement Ratio


In [26]:
exp = expms['results/result_iterations_5001_generation_time_4_elitism_20_genome_size_16-12-2_remove_dead_organisms_True']

org_loc = exp['org_loc']

eaten_stats = exp['eaten_stat']

In [20]:
f"Total number of organisms in the experiment {org_loc['index'].nunique()}"

'Total number of organisms in the experiment 20040'

In [45]:
# total_movements = org_loc.groupby('index')['iteration'].nunique()
# total_movements
total_movements = org_loc.groupby(['index', 'iteration']).size().groupby(level=0).count()
total_movements

index
0        4
1        4
2        4
3        4
4        4
        ..
20035    1
20036    1
20037    1
20038    1
20039    1
Length: 20040, dtype: int64

In [46]:
total_food_acquisitions = eaten_stats.groupby('organism_id').size()
total_food_acquisitions

organism_id
35       2
85       2
120      2
123      2
144      2
        ..
19858    2
19896    2
19962    2
19971    2
19985    2
Length: 1319, dtype: int64

In [57]:
total_food_acquisitions.describe()

count    1319.000000
mean        2.247157
std         0.765050
min         2.000000
25%         2.000000
50%         2.000000
75%         2.000000
max         8.000000
dtype: float64

In [58]:
total_food_acquisitions[total_food_acquisitions == total_food_acquisitions.max()]

organism_id
14106    8
19017    8
dtype: int64

In [52]:
food_to_movement_ratio = total_movements / total_food_acquisitions
food_to_movement_ratio = food_to_movement_ratio.fillna(np.inf)

food_to_movement_ratio[food_to_movement_ratio > 0]

0        inf
1        inf
2        inf
3        inf
4        inf
        ... 
20035    inf
20036    inf
20037    inf
20038    inf
20039    inf
Length: 20040, dtype: float64

In [56]:
(food_to_movement_ratio.idxmin(), food_to_movement_ratio.min())

(19985, 6.5)

In [54]:
eaten_stats[eaten_stats['organism_id'] == food_to_movement_ratio.idxmin()]

organism_id  food_location  energy_taken  iteration
1632        19985      13.842600             1       4992
1633        19985      13.553471             1       4992

In [37]:
fig = go.Figure(data=go.Bar(x=food_to_movement_ratio.index, y=food_to_movement_ratio.values))
fig.update_layout(title_text='Food-to-Movement Ratio by Organism', xaxis_title='Organism ID', yaxis_title='Food-to-Movement Ratio')
fig.show()


In [38]:
movements_per_time = org_loc.groupby(['index', 'iteration']).size()
food_acquisitions_per_time = eaten_stats.groupby(['organism_id', 'iteration']).size()

ratio_per_time = movements_per_time / food_acquisitions_per_time
ratio_per_time = ratio_per_time.fillna(0)


In [39]:
fig = go.Figure()
for organism in ratio_per_time.index.get_level_values('index').unique():
    fig.add_trace(go.Scatter(x=ratio_per_time.loc[organism].index, y=ratio_per_time.loc[organism].values, mode='lines', name=str(organism)))

fig.update_layout(title_text='Evolution of Food-to-Movement Ratio Over Time', xaxis_title='Iteration', yaxis_title='Food-to-Movement Ratio')
fig.show()


KeyError: 5001

In [44]:
# Calculate the total movements and food acquisitions at each time step
movements_per_time = org_loc.groupby(['index', 'iteration']).size()
food_acquisitions_per_time = eaten_stats.groupby(['organism_id', 'iteration']).size()

# print(movements_per_time.)

# Calculate the Food-to-Movement ratio at each time step
ratio_per_time = movements_per_time / food_acquisitions_per_time

# Fill in any missing values
ratio_per_time = ratio_per_time.fillna(0)

print(ratio_per_time)

# Find the organisms with the worst and best Food-to-Movement ratio at each time step
worst_ratio = ratio_per_time.idxmax()
best_ratio = ratio_per_time.idxmin()

print(worst_ratio)
print(best_ratio)

# Create a plotly graph
fig = go.Figure()

# Plot the worst ratio
fig.add_trace(go.Scatter(x=worst_ratio.index, y=worst_ratio.values, mode='lines', name='Worst Ratio', line=dict(color='firebrick')))

# Plot the best ratio
fig.add_trace(go.Scatter(x=best_ratio.index, y=best_ratio.values, mode='lines', name='Best Ratio', line=dict(color='royalblue')))

fig.update_layout(title_text='Evolution of Worst and Best Food-to-Movement Ratio Over Time', xaxis_title='Iteration', yaxis_title='Food-to-Movement Ratio')

fig.show()


index  iteration
0      0            1
       1            1
       2            1
       3            1
1      0            1
                   ..
20035  5000         1
20036  5000         1
20037  5000         1
20038  5000         1
20039  5000         1
Length: 155067, dtype: int64
iteration  index  organism_id
0          0      NaN            0.0
           1      NaN            0.0
           2      NaN            0.0
           3      NaN            0.0
           4      NaN            0.0
                                ... 
5000       20035  NaN            0.0
           20036  NaN            0.0
           20037  NaN            0.0
           20038  NaN            0.0
           20039  NaN            0.0
Length: 163096, dtype: float64
(1, 0, 35)
(0, 0, nan)


AttributeError: 'tuple' object has no attribute 'values'